# Mesterséges neurális hálók tanítása tensorflow-val

A mai gyakorlaton egy két rejtett réteges neuronháló tanítunk kézzel írt számok felismerésére.

## Neuronháló

![Neuronháló](https://upload.wikimedia.org/wikipedia/commons/thumb/4/46/Colored_neural_network.svg/300px-Colored_neural_network.svg.png)

## MNIST adatbázis

![MNIST adatbázis](http://neuralnetworksanddeeplearning.com/images/mnist_100_digits.png)
Az adatbázis kézzel írt számokról készült képeket tartalmaz. Összesen 60000 db példa található a tanító adatbázisban és 10000 a teszt halmazban. A képeket egységes méretre hozták (28x28 pixel) és minden pixel intenzitását 0 és 1 közé normalizáltak. A képek 1-D-s numpy tömbökben vannak tárolva.

Bővebben: http://yann.lecun.com/exdb/mnist/

Első lépésben telepítsük a matplotlib csomagot, majd improtáljuk a szükséges csomagokat és letöltjük az adatbázist

In [ ]:
!sudo pip3 install matplotlib

In [ ]:
from __future__ import print_function
import tensorflow as tf
import matplotlib.pyplot as plt
import numpy as np

# Import MNIST data
mnist = tf.keras.datasets.mnist

(x_train, y_train),(x_test, y_test) = mnist.load_data()
# flatten for training
x_train = x_train.reshape(x_train.shape[0], x_train.shape[1]*x_train.shape[2])
x_test = x_test.reshape(x_test.shape[0], x_test.shape[1]*x_test.shape[2])
# normalization
x_train, x_test = x_train / 255.0, x_test / 255.0

print(x_train.shape, y_train.shape)

A következő lépés a tanítási paraméterek és a neuronháló strukturához a változók inicializálása.

In [ ]:
# Parameters
learning_rate = 0.1
num_steps = 1000
batch_size = 128
display_step = 100

# Network Parameters
n_hidden_1 = 256 # 1st layer number of neurons
n_hidden_2 = 256 # 2nd layer number of neurons
num_input = 784 # MNIST data input (img shape: 28*28)
num_classes = 10 # MNIST total classes (0-9 digits)

y_train_one_hot = np.eye(num_classes)[y_train]
y_test_one_hot = np.eye(num_classes)[y_test]

A neuronháló tanításához létrehozunk egy bemeneti függvényt, ami a korábba letöltött adatbázisból ú.n. batch-eket fog készíteni.

In [ ]:
# Define the input function for training
input_fn = tf.estimator.inputs.numpy_input_fn(
    x={'images': x_train}, y=y_train,
    batch_size=batch_size, num_epochs=None, shuffle=True)

A következő kód létrehozza a 2 rejtett réteges hálózatot, lineáris aktivációs függvénnyel.

In [ ]:
# Define the neural network
def neural_net(x_dict):
    # TF Estimator input is a dict, in case of multiple inputs
    x = x_dict['images']
    # Hidden fully connected layer with 256 neurons
    layer_1 = tf.layers.dense(x, n_hidden_1)
    # Hidden fully connected layer with 256 neurons
    layer_2 = tf.layers.dense(layer_1, n_hidden_2)
    # Output fully connected layer with a neuron for each class
    out_layer = tf.layers.dense(layer_2, num_classes)
    return out_layer

A tanításhoz szükséges dolgok beállítása:
- neuronháló kimenetének kezelése
- loss függvény megadása
- hibametrika választása

In [ ]:
# Define the model function (following TF Estimator Template)
def model_fn(features, labels, mode):
    
    # Build the neural network
    logits = neural_net(features)
    
    # Predictions
    pred_classes = tf.argmax(logits, axis=1)
    pred_probs = tf.nn.softmax(logits)
    
    # If prediction mode, early return
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode, predictions=pred_classes) 
        
    # Define loss and optimizer
    loss_op = tf.reduce_mean(tf.nn.sparse_softmax_cross_entropy_with_logits(
        logits=logits, labels=tf.cast(labels, dtype=tf.int32)))
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=learning_rate)
    train_op = optimizer.minimize(loss_op, global_step=tf.train.get_global_step())
    
    # Evaluate the accuracy of the model
    acc_op = tf.metrics.accuracy(labels=labels, predictions=pred_classes)
    
    # TF Estimators requires to return a EstimatorSpec, that specify
    # the different ops for training, evaluating, ...
    estim_specs = tf.estimator.EstimatorSpec(
      mode=mode,
      predictions=pred_classes,
      loss=loss_op,
      train_op=train_op,
      eval_metric_ops={'accuracy': acc_op})

    return estim_specs

A fenti kódok meghívása, estimator létrehozása.

In [ ]:
# Build the Estimator
model = tf.estimator.Estimator(model_fn)

### Neuronháló tanítása
Megfigyelhető, hogy minden 100. step után közöl információt és 1000 lépésig fut (ezeket feljebb állítottuk be).
Tanítás során célszerű figyelni a loss értékét, az alapján tudjuk beállítani a tanulási paramétereket.

In [ ]:
# Train the Model
model.train(input_fn, steps=num_steps)

Tanítás után kiértékelünk a teszt halmazon.
**Fontos: csak a legjobb modellünket értékeljük ki a teszt halmazon, különben peeking-elünk.**

Peeking (kukucskálás): a teszt halmazon látott teljesítmény alapján optimalizáljuk az algoritmusunk paramétereit ezért nem tudjuk hogy az milyen jól általánosít.

In [ ]:
# Evaluate the Model
# Define the input function for evaluating
input_fn_test = tf.estimator.inputs.numpy_input_fn(
    x={'images': x_test}, y=y_test,
    batch_size=batch_size, shuffle=False)
# Use the Estimator 'evaluate' method
model.evaluate(input_fn_test)

Kiértékelhetünk csak néhány példát is a következő módon:

In [ ]:
# Predict single images
n_images = 4
# Get images from test set
test_images = x_test[:n_images]
# Prepare the input data
input_fn_test_few = tf.estimator.inputs.numpy_input_fn(
    x={'images': test_images}, shuffle=False)
# Use the model to predict the images class
preds = list(model.predict(input_fn_test_few))

# Display
for i in range(n_images):
    plt.imshow(np.reshape(test_images[i], [28, 28]), cmap='gray')
    plt.show()
    print("Model prediction:", preds[i])

### Feladatok
1. Keressük meg, hogy mely képeken hibázott a háló!
2. Változtassuk a neuronok számát, a batch méretet és a num_step értékét!
3. Adjunk hozzá a neuronhálóhoz további rejtett rétegeket!